In [3]:
import sys
sys.path.insert(0, '..')

import spinesTS
print("spinesTS version: ", spinesTS.__version__)

from spinesTS.preprocessing import split_series
from spinesTS.plotting import plot2d
from sklearn.metrics import r2_score
import pandas as pd
from sklearn.preprocessing import MinMaxScaler

from spinesTS.data import BuiltInSeriesData
from spinesTS.nn import *
from spinesTS.metrics import mean_absolute_error, wmape
from spinesTS.metrics import mean_absolute_percentage_error
from tqdm.auto import tqdm


class BenchMarks:
    def __init__(self, in_features, out_features, train_size=0.8):
        self.series_data = BuiltInSeriesData(print_file_list=False)
        self.in_features = in_features
        self.out_features = out_features
        self.train_size = train_size

        self.res_dataframe = pd.DataFrame(columns=['dataset', 'mae', 'wmape', 'r2'])


    def data_process(self):
        for (name, (date_col, target_col)) in {
            'AirPassengers':('Month', '#Passengers'), 
            'ETTh1':('date', 'OT'), 
            'ETTh2':('date', 'OT'),
            'ETTm1':('date', 'OT'), 
            'ETTm2':('date', 'OT'),
            'Electric_Production':('date', 'value'), 
            'Messages_Sent':('date', 'ta'), 
            'Messages_Sent_Hour':('date', 'ta'),
            'Supermarket_Incoming':('date', 'goods_cnt'), 
            'Web_Sales':('date', 'type_a')
        }.items():
            cs = self.series_data[name]
            x_train, x_test, y_train, y_test = split_series(cs[target_col], cs[target_col], 
                                                            self.in_features, self.out_features, train_size=self.train_size)
            yield name, x_train, x_test, y_train, y_test

    def train(self, models_list):
        for (model_name, model) in tqdm(models_list, desc="models"):
            for dataset_name, x_train, x_test, y_train, y_test in tqdm(self.data_process(), total=10, desc="fitting on datasets"):

                scaler = MinMaxScaler()
                x_train = scaler.fit_transform(x_train)
                x_test = scaler.transform(x_test)
                
                scaler2 = MinMaxScaler()
                y_train = scaler2.fit_transform(y_train)
                y_test = scaler2.transform(y_test)
                print('x_train shape:', x_train.shape, ' x_test shape:', x_test.shape)

                model.fit(x_train, y_train, eval_set=(x_test, y_test), batch_size=12288, min_delta=0,
                          patience=100, epochs=3000, verbose=True)
                
                y_pred_inverse = scaler2.inverse_transform(model.predict(x_test))
                
                y_test_inverse = scaler2.inverse_transform(y_test)

                res = pd.DataFrame({
                    "dataset": dataset_name,
                    "mae": mean_absolute_error(y_test_inverse, y_pred_inverse),
                    "wmape": wmape(y_test_inverse, y_pred_inverse),
                    "r2": r2_score(y_test_inverse.T, y_pred_inverse.T)
                }, index=[model_name])

                self.res_dataframe = pd.concat((self.res_dataframe, res), axis=0)

spinesTS version:  0.4.0


In [5]:
models_list = [
    ('pos_gau', PosGauNet(60, 30, random_seed=42, learning_rate=0.001, level=2, device='mps')),
    ('gau', GAUNet(60, 30, random_seed=42, learning_rate=0.001, level=2, device='cpu'))
    
]

benchmarks = BenchMarks(60, 30)

benchmarks.train(models_list)

Epoch 636/3000  
2/2 - p9 -  [*lr: 9.55e-05] - loss: 0.0306 - mae: 0.0306 - val_loss: 0.0300 - val_mae: 0.0300 - 0.37s/epoch - 0.187s/step
Epoch 637/3000  
2/2 - p0 -  [*lr: 0.0003455] - loss: 0.0306 - mae: 0.0306 - val_loss: 0.0298 - val_mae: 0.0298 - 0.39s/epoch - 0.196s/step
Epoch 638/3000  
2/2 - p1 -  [*lr: 0.0006545] - loss: 0.0309 - mae: 0.0309 - val_loss: 0.0305 - val_mae: 0.0305 - 0.38s/epoch - 0.191s/step
Epoch 639/3000  
2/2 - p2 -  [*lr: 0.0009045] - loss: 0.0309 - mae: 0.0309 - val_loss: 0.0308 - val_mae: 0.0308 - 0.40s/epoch - 0.198s/step
Epoch 640/3000  
2/2 - p3 - loss: 0.0313 - mae: 0.0313 - val_loss: 0.0303 - val_mae: 0.0303 - 0.38s/epoch - 0.191s/step
Epoch 641/3000  
2/2 - p4 -  [*lr: 0.0009045] - loss: 0.0309 - mae: 0.0309 - val_loss: 0.0302 - val_mae: 0.0302 - 0.31s/epoch - 0.156s/step
Epoch 642/3000  
2/2 - p5 -  [*lr: 0.0006545] - loss: 0.0313 - mae: 0.0313 - val_loss: 0.0300 - val_mae: 0.0300 - 0.40s/epoch - 0.200s/step
Epoch 643/3000  
2/2 - p6 -  [*lr: 0.0003

MPS  available: True  | MPS  use: True
CUDA available: False | CUDA use: False
CPU  available: True  | CPU  use: False


Epoch 1/3000  
2/2 - p0 -  [*lr: 0.0009045] - loss: 0.0419 - mae: 0.0419 - val_loss: 0.0519 - val_mae: 0.0519 - 1.15s/epoch - 0.575s/step
Epoch 2/3000  
2/2 - p1 -  [*lr: 0.0006545] - loss: 0.0442 - mae: 0.0442 - val_loss: 0.0526 - val_mae: 0.0526 - 0.35s/epoch - 0.174s/step
Epoch 3/3000  
2/2 - p0 -  [*lr: 0.0003455] - loss: 0.0418 - mae: 0.0418 - val_loss: 0.0506 - val_mae: 0.0506 - 966.01s/epoch - 483.007s/step
Epoch 4/3000  
2/2 - p0 -  [*lr: 9.55e-05] - loss: 0.0422 - mae: 0.0422 - val_loss: 0.0500 - val_mae: 0.0500 - 0.46s/epoch - 0.232s/step
Epoch 5/3000  
2/2 - p1 - [*lr: 0.000000e+00] - loss: 0.0409 - mae: 0.0409 - val_loss: 0.0502 - val_mae: 0.0502 - 0.44s/epoch - 0.222s/step
Epoch 6/3000  
2/2 - p2 -  [*lr: 9.55e-05] - loss: 0.0407 - mae: 0.0407 - val_loss: 0.0502 - val_mae: 0.0502 - 0.46s/epoch - 0.229s/step
Epoch 7/3000  
2/2 - p3 -  [*lr: 0.0003455] - loss: 0.0407 - mae: 0.0407 - val_loss: 0.0501 - val_mae: 0.0501 - 0.63s/epoch - 0.313s/step
Epoch 8/3000  
2/2 - p4 -  [*l

MPS  available: True  | MPS  use: True
CUDA available: False | CUDA use: False
CPU  available: True  | CPU  use: False


Epoch 1/3000  
1/1 - p0 -  [*lr: 0.0009045] - loss: 0.1026 - mae: 0.1026 - val_loss: 0.1306 - val_mae: 0.1306 - 0.71s/epoch - 0.712s/step
Epoch 2/3000  
1/1 - p1 -  [*lr: 0.0006545] - loss: 0.1003 - mae: 0.1003 - val_loss: 0.1408 - val_mae: 0.1408 - 0.06s/epoch - 0.062s/step
Epoch 3/3000  
1/1 - p2 -  [*lr: 0.0003455] - loss: 0.1020 - mae: 0.1020 - val_loss: 0.1410 - val_mae: 0.1410 - 0.06s/epoch - 0.061s/step
Epoch 4/3000  
1/1 - p3 -  [*lr: 9.55e-05] - loss: 0.1019 - mae: 0.1019 - val_loss: 0.1372 - val_mae: 0.1372 - 0.06s/epoch - 0.059s/step
Epoch 5/3000  
1/1 - p4 - [*lr: 0.000000e+00] - loss: 0.1008 - mae: 0.1008 - val_loss: 0.1356 - val_mae: 0.1356 - 0.06s/epoch - 0.062s/step
Epoch 6/3000  
1/1 - p5 -  [*lr: 9.55e-05] - loss: 0.1004 - mae: 0.1004 - val_loss: 0.1356 - val_mae: 0.1356 - 0.06s/epoch - 0.058s/step
Epoch 7/3000  
1/1 - p6 -  [*lr: 0.0003455] - loss: 0.1004 - mae: 0.1004 - val_loss: 0.1332 - val_mae: 0.1332 - 0.06s/epoch - 0.058s/step
Epoch 8/3000  
1/1 - p0 -  [*lr: 0

...

Epoch 1/3000  
1/1 - p0 -  [*lr: 0.0008181] - loss: 0.1534 - mae: 0.1534 - val_loss: 0.1345 - val_mae: 0.1345 - 0.11s/epoch - 0.108s/step
Epoch 2/3000  
1/1 - p1 -  [*lr: 0.000592] - loss: 0.1530 - mae: 0.1530 - val_loss: 0.1398 - val_mae: 0.1398 - 0.09s/epoch - 0.088s/step
Epoch 3/3000  
1/1 - p2 -  [*lr: 0.0003125] - loss: 0.1575 - mae: 0.1575 - val_loss: 0.1442 - val_mae: 0.1442 - 0.08s/epoch - 0.080s/step
Epoch 4/3000  
1/1 - p3 -  [*lr: 8.64e-05] - loss: 0.1612 - mae: 0.1612 - val_loss: 0.1454 - val_mae: 0.1454 - 0.08s/epoch - 0.083s/step
Epoch 5/3000  
1/1 - p4 - [*lr: 0.000000e+00] - loss: 0.1621 - mae: 0.1621 - val_loss: 0.1454 - val_mae: 0.1454 - 0.16s/epoch - 0.164s/step
Epoch 6/3000  
1/1 - p5 -  [*lr: 9.55e-05] - loss: 0.1620 - mae: 0.1620 - val_loss: 0.1454 - val_mae: 0.1454 - 0.08s/epoch - 0.083s/step
Epoch 7/3000  
1/1 - p6 -  [*lr: 0.0003455] - loss: 0.1620 - mae: 0.1620 - val_loss: 0.1445 - val_mae: 0.1445 - 0.09s/epoch - 0.086s/step
Epoch 8/3000  
1/1 - p7 -  [*lr: 0.

MPS  available: True  | MPS  use: False
CUDA available: False | CUDA use: False
CPU  available: True  | CPU  use: True


Epoch 1/3000  
1/1 - p0 -  [*lr: 0.0009045] - loss: 0.1281 - mae: 0.1281 - val_loss: 0.1245 - val_mae: 0.1245 - 0.03s/epoch - 0.031s/step
Epoch 2/3000  
1/1 - p0 -  [*lr: 0.0006545] - loss: 0.1281 - mae: 0.1281 - val_loss: 0.1229 - val_mae: 0.1229 - 0.02s/epoch - 0.017s/step
Epoch 3/3000  
1/1 - p0 -  [*lr: 0.0003455] - loss: 0.1277 - mae: 0.1277 - val_loss: 0.1210 - val_mae: 0.1210 - 0.01s/epoch - 0.014s/step
Epoch 4/3000  
1/1 - p0 -  [*lr: 9.55e-05] - loss: 0.1272 - mae: 0.1272 - val_loss: 0.1193 - val_mae: 0.1193 - 0.01s/epoch - 0.013s/step
Epoch 5/3000  
1/1 - p0 - [*lr: 0.000000e+00] - loss: 0.1261 - mae: 0.1261 - val_loss: 0.1186 - val_mae: 0.1186 - 0.01s/epoch - 0.013s/step
Epoch 6/3000  
1/1 - p1 -  [*lr: 9.55e-05] - loss: 0.1256 - mae: 0.1256 - val_loss: 0.1186 - val_mae: 0.1186 - 0.01s/epoch - 0.012s/step
Epoch 7/3000  
1/1 - p0 -  [*lr: 0.0003455] - loss: 0.1256 - mae: 0.1256 - val_loss: 0.1176 - val_mae: 0.1176 - 0.01s/epoch - 0.014s/step
Epoch 8/3000  
1/1 - p0 -  [*lr: 0

MPS  available: True  | MPS  use: False
CUDA available: False | CUDA use: False
CPU  available: True  | CPU  use: True


Epoch 1/3000  
1/1 - p0 -  [*lr: 0.0009045] - loss: 0.2142 - mae: 0.2142 - val_loss: 0.3425 - val_mae: 0.3425 - 0.07s/epoch - 0.070s/step
Epoch 2/3000  
1/1 - p0 -  [*lr: 0.0006545] - loss: 0.1840 - mae: 0.1840 - val_loss: 0.2908 - val_mae: 0.2908 - 0.04s/epoch - 0.038s/step
Epoch 3/3000  
1/1 - p0 -  [*lr: 0.0003455] - loss: 0.1466 - mae: 0.1466 - val_loss: 0.2454 - val_mae: 0.2454 - 0.04s/epoch - 0.036s/step
Epoch 4/3000  
1/1 - p0 -  [*lr: 9.55e-05] - loss: 0.1263 - mae: 0.1263 - val_loss: 0.2215 - val_mae: 0.2215 - 0.04s/epoch - 0.039s/step
Epoch 5/3000  
1/1 - p0 - [*lr: 0.000000e+00] - loss: 0.1225 - mae: 0.1225 - val_loss: 0.2156 - val_mae: 0.2156 - 0.04s/epoch - 0.039s/step
Epoch 6/3000  
1/1 - p1 -  [*lr: 9.55e-05] - loss: 0.1221 - mae: 0.1221 - val_loss: 0.2156 - val_mae: 0.2156 - 0.04s/epoch - 0.036s/step
Epoch 7/3000  
1/1 - p0 -  [*lr: 0.0003455] - loss: 0.1221 - mae: 0.1221 - val_loss: 0.2111 - val_mae: 0.2111 - 0.04s/epoch - 0.038s/step
Epoch 8/3000  
1/1 - p0 -  [*lr: 0

In [6]:
benchmarks.res_dataframe

dataset           mae     wmape         r2
pos_gau         AirPassengers     33.669062  0.079909   0.649273
pos_gau                 ETTh1      1.518148  0.196651  -2.386909
pos_gau                 ETTh2      3.300314  0.126934  -1.796143
pos_gau                 ETTm1      1.486806  0.149195  -3.869110
pos_gau                 ETTm2      2.303874  0.116597  -7.867338
pos_gau   Electric_Production      3.633493  0.035491   0.751144
pos_gau         Messages_Sent  30017.306108  0.213821  -1.224671
pos_gau    Messages_Sent_Hour   2355.171758  0.444651   0.432429
pos_gau  Supermarket_Incoming   6107.019978  0.143855  -0.098478
pos_gau             Web_Sales   3738.559604  0.247101 -12.567400
gau             AirPassengers     25.992987  0.061691   0.794653
gau                     ETTh1      1.486759  0.192585  -2.035322
gau                     ETTh2      3.184004  0.122460  -1.538447
gau                     ETTm1      1.406757  0.141162  -3.198272
gau                     ETTm2      2.087638  0.105654  -6.577579
gau       Electric_Production      3.856600  0.037670   0.725409
gau             Messages_Sent  28460.919094  0.202734  -0.994048
gau        Messages_Sent_Hour   1605.141667  0.303047   0.706205
gau      Supermarket_Incoming   5746.017686  0.135351   0.004115
gau                 Web_Sales   3927.004502  0.259556 -13.803621